In [2]:
from loader import *
from fastNLP.io import ChnSentiCorpLoader
from fastNLP import DataSet
from fastNLP import Vocabulary
from fastNLP.io import ChnSentiCorpPipe, DataBundle
from spacy.lang.zh import Chinese
import spacy
from fastNLP.embeddings import StaticEmbedding, StackEmbedding
import pandas as pd
from sklearn.utils import shuffle
from sklearn.model_selection import KFold
import numpy as np
from torch import nn
import re

# nlp = Chinese()
# nlp = Chinese.from_config({"nlp": {"tokenizer":{"segmenter": "pkuseg"}}})
# nlp.tokenizer.initialize(pkuseg_model="mixed", pkuseg_user_dict='./data/dict.txt')
from prepare_data import nlp, role_map

In [3]:
doc, q, cho, ans = json_parser('./data/val_fold1.json')
raw_chars = {
        'raw_text': doc,
        'cho'     : cho,
        'q'       : q,
}
ds = DataSet(raw_chars)


In [4]:
from ckiptagger import data_utils, construct_dictionary, WS, POS, NER

ws = WS("./data")
word_to_weight = {
    "土地公": 1,
    "土地婆": 1,
}
dictionary = construct_dictionary(word_to_weight)



/home/rockyo/anaconda3/envs/aicup/lib/python3.7/site-packages/tensorflow/python/keras/layers/legacy_rnn/rnn_cell_impl.py:909: UserWarning: `tf.nn.rnn_cell.LSTMCell` is deprecated and will be removed in a future version. This class is equivalent as `tf.keras.layers.LSTMCell`, and will be replaced by that in Tensorflow 2.0.
  warnings.warn("`tf.nn.rnn_cell.LSTMCell` is deprecated and will be "
/home/rockyo/anaconda3/envs/aicup/lib/python3.7/site-packages/tensorflow/python/keras/engine/base_layer_v1.py:1700: UserWarning: `layer.add_variable` is deprecated and will be removed in a future version. Please use `layer.add_weight` method instead.
  warnings.warn('`layer.add_variable` is deprecated and '


In [97]:
import jieba


with open('./data/illness.txt') as f:
    other_clinic = f.read().split('\n')
    other_clinic = list(set(other_clinic))

    
[jieba.lcut(c) for c in other_clinic if len(jieba.lcut(c))>1]
jieba.lcut('約炮')

['約炮']

In [6]:
word_sentence_list

NameError: name 'word_sentence_list' is not defined

In [8]:
data_utils.download_data_gdown("./")

Downloading...
From: https://drive.google.com/uc?id=1efHsY16pxK0lBD2gYCgCTnv1Swstq771
To: /home/rockyo/aicup/data.zip
1.88GB [03:09, 9.92MB/s]


In [9]:
doc[0][0]

'<1>嗯，<1>對，<1>目前是還好，<1>沒有什麼特別的問題。<4>好，<4>那你當初為什麼會想要來吃PrEP？<1>當初為什麼會想要來吃PrEP。<4>對。<1>欸，<1>就，<4>對。<4>然後你接下來。<1>嗯。<4>我上次有跟你提到，<4>就是如果你開始吃PrEP的話，<4>要每天上網填寫。<1>喔，<1>對，<1>這個是。<4>你有印象嗎？<1>嗯。<4>你就會被電腦移除。<1>七次是什麼意思？<4>就是說我七次沒有上去打卡，<4>等於我累積七天沒有上去打卡。<1>喔，<1>連續嗎，<1>還是？<4>我就會被，<1>喔，<1>連續嗎，<1>還是？<4>我就會被，<4>連續。<4>我就會被系統移除。<1>是。<4>這樣我就，<4>我們就沒有辦法救你了。<4>也就是說系統移除就是，'

In [10]:
doc[0][0].split('<')

['',
 '1>嗯，',
 '1>對，',
 '1>目前是還好，',
 '1>沒有什麼特別的問題。',
 '4>好，',
 '4>那你當初為什麼會想要來吃PrEP？',
 '1>當初為什麼會想要來吃PrEP。',
 '4>對。',
 '1>欸，',
 '1>就，',
 '4>對。',
 '4>然後你接下來。',
 '1>嗯。',
 '4>我上次有跟你提到，',
 '4>就是如果你開始吃PrEP的話，',
 '4>要每天上網填寫。',
 '1>喔，',
 '1>對，',
 '1>這個是。',
 '4>你有印象嗎？',
 '1>嗯。',
 '4>你就會被電腦移除。',
 '1>七次是什麼意思？',
 '4>就是說我七次沒有上去打卡，',
 '4>等於我累積七天沒有上去打卡。',
 '1>喔，',
 '1>連續嗎，',
 '1>還是？',
 '4>我就會被，',
 '1>喔，',
 '1>連續嗎，',
 '1>還是？',
 '4>我就會被，',
 '4>連續。',
 '4>我就會被系統移除。',
 '1>是。',
 '4>這樣我就，',
 '4>我們就沒有辦法救你了。',
 '4>也就是說系統移除就是，']

In [11]:
ds

+-------------------------------+-------------------------------+-------------------------------+
| raw_text                      | cho                           | q                             |
+-------------------------------+-------------------------------+-------------------------------+
| ['<1>嗯，<1>對，<1>目前是...  | ['累積七天沒有上去打卡不會... | 關於吃PrEP要上網填寫的系統... |
| ['<2>但是今天會有抽血單，...  | ['想吐', '情緒低落', '沒有... | 請問民眾吃完藥物的副作用下... |
| ['<2>可是又有吃，<2>吃了幾... | ['有固定的伴侶', '伴侶是感... | 關於民眾敘述，何者錯誤？      |
| ['<1>了解。<4>好。<4>這一...  | ['抽藥物濃度', '抽兩支血'...  | 下列何者不是民眾今天要做的... |
| ['<4>所以其實你在吃PrEP的...  | ['近幾個月開始會有一些約炮... | 下列敘述何者錯誤？            |
| ['<1>就是……<2>還是一樣？...   | ['水分喝多對泌尿道感染是有... | 請問關於泌尿道感染，下列何... |
| ['<2>好。<2>那所以，<2>那...  | ['以前吃過暴露前預防', '通... | 關於民眾的狀態下列何者正確... |
| ['<4>你有沒有什麼疑問想問...  | ['梅毒', '愛滋病', 'B型肝...  | 請問民眾得過何種疾病？        |
| ['<1>真的，<1>真的太忙了。... | ['8月', '7月', '三個月']      | 請問醫師建議民眾多久去匿篩... |
| ['<1>半年。<4>半年的藥。<...  | ['民眾都無套', '民眾每天吃... | 關於民眾的敘述，何者正確？... |
| ['<1>有沒有吃還是會慢慢緊...  | 

In [32]:
def tokenize(ins):
    role_ins = []
    ins_frag = []
    for frag in ins:
        print(frag)
        roleid = []
        tokenize_sen = []
        sents = doc[0][0].split('<')[1:]
        for s in sents:
            sid =s[0]
            # print(s[3:], '\n')
            s = [ele.text for ele in nlp.tokenizer.pipe(s[2:])]
            roleid += [sid] * len(s)
            tokenize_sen+=s

        role_ins.append(roleid)
        ins_frag.append(tokenize_sen)
        assert len(roleid) == len(tokenize_sen)
    return {
        'raw_text': ins_frag,
        'roleid' :role_ins,
    }

In [ ]:
bined_query_cho = False


def build_ds(f):
    doc, q, cho, ans = json_parser(f)
    if bined_query_cho :
        cho = [[q[i]+ele for ele in sublist] for i, sublist in enumerate(cho) ]
    raw_chars = {
        'raw_text': doc,
        'cho'     : cho,
        'q'       : q,
    }
    if not ans == []:
        ans= [ele['qa'] for ele in ans] 
        ans_onehot =[np.eye(3)[ele] for ele in ans]
        raw_chars.update({'target':ans, 'target_onehot':ans_onehot})

    ds = DataSet(raw_chars)
    ds.apply_field_more(tokenize, field_name='raw_text', is_input=True,)
    # for k in ['raw_text', 'cho']:
    ds.apply_field(
        lambda ins: [[ele.text for ele in nlp.tokenizer.pipe(sublist)] for sublist in ins], 
        field_name='cho',
        new_field_name='cho', 
        is_input=True
        )
    ds.apply_field(
        lambda ins: [ele.text for ele in nlp.tokenizer.pipe(ins)], 
        field_name='q',
        new_field_name='q', 
        is_input=True
    )    
    if not ans==[]:
        ds.set_input('target_onehot')
        ds.set_target('target') 
    return ds   


ds = {}
train = './data/train_foldidx.json'
val = './data/val_foldidx.json'

for i in range(5):
    ds.update({
        f'train{i}' : build_ds(train.replace('idx', str(i))),
        f'val{i}'   : build_ds(val.replace('idx', str(i))),
    })
ds['dev'] = build_ds('./data/Develop_bined.json')


['<1>嗯，<1>對，<1>目前是還好，<1>沒有什麼特別的問題。<4>好，<4>那你當初為什麼會想要來吃PrEP？<1>當初為什麼會想要來吃PrEP。<4>對。<1>欸，<1>就，<4>對。<4>然後你接下來。<1>嗯。<4>我上次有跟你提到，<4>就是如果你開始吃PrEP的話，<4>要每天上網填寫。<1>喔，<1>對，<1>這個是。<4>你有印象嗎？<1>嗯。<4>你就會被電腦移除。<1>七次是什麼意思？<4>就是說我七次沒有上去打卡，<4>等於我累積七天沒有上去打卡。<1>喔，<1>連續嗎，<1>還是？<4>我就會被，<1>喔，<1>連續嗎，<1>還是？<4>我就會被，<4>連續。<4>我就會被系統移除。<1>是。<4>這樣我就，<4>我們就沒有辦法救你了。<4>也就是說系統移除就是，', '<1>嗯，<1>對，<1>目前是還好，<1>沒有什麼特別的問題。<4>好，<4>那你當初為什麼會想要來吃PrEP？<1>當初為什麼會想要來吃PrEP。<4>對。<1>欸，<1>就，<4>對。<4>然後你接下來。<1>嗯。<4>我上次有跟你提到，<4>就是如果你開始吃PrEP的話，<4>要每天上網填寫。<1>喔，<1>對，<1>這個是。<4>你有印象嗎？<1>嗯。<4>好，<4>這個。<1>嗯。<4>你每天上網填寫，<4>你明天可能還是沒有辦法。<1>嗯。<4>因為明天藥局才剛領藥，<4>所以它，<1>是。<4>對，<4>然後後天應該就可以打開了。<4>你就會上網進去，<4>你就填每天的服藥紀錄，<4>它裡面會有你今天有沒有服藥跟有沒有性行為。<1>是。<4>這樣OK嗎？', '<1>沒有問題，<1>沒關係。<4>好喔好喔。<4>所以，<4>痾，<4>你這樣子回去之後，<4>痾，<4>經過上一次跟你解釋PrEP的。<1>民眾，<1>嗯。<4>的使用。<1>是。<4>那你有沒有什麼問題想問我？<1>嗯，<4>那你有沒有什麼問題想問我？<1>嗯，<1>對，<1>目前是還好，<1>沒有什麼特別的問題。<4>好，<4>那你當初為什麼會想要來吃PrEP？<1>當初為什麼會想要來吃PrEP。<4>對。<1>欸，<1>就，<1>就覺得目前沒有固定的對象啊。<4>還是會用保險套去阻隔這些事情真的比較，<4>雙重保障，<4>對。<4>然後你接下來。<1>嗯。<4>我上次有跟你提到，<4>就

In [39]:
ds['dev']

+------------------------+------------------------+------------------------+------------------------+
| raw_text               | cho                    | q                      | roleid                 |
+------------------------+------------------------+------------------------+------------------------+
| [['嗯', '，', '對',... | [['性', '行', '為',... | ['請', '問', '任', ... | [['1', '1', '1', '1... |
| [['嗯', '，', '對',... | [['下', '一', '次',... | ['下', '列', '何', ... | [['1', '1', '1', '1... |
| [['嗯', '，', '對',... | [['有', '固', '定',... | ['請', '問', '關', ... | [['1', '1', '1', '1... |
| [['嗯', '，', '對',... | [['B', '肝'], ['H',... | ['下', '列', '何', ... | [['1', '1', '1', '1... |
| [['嗯', '，', '對',... | [['三', '個', '月']... | ['請', '問', '個', ... | [['1', '1', '1', '1... |
| [['嗯', '，', '對',... | [['有', '性', '行',... | ['下', '列', '何', ... | [['1', '1', '1', '1... |
| [['嗯', '，', '對',... | [['很', '在', '意',... | ['請', '問', '民', ... | [['1', '1', '1', '1... |
| [['嗯', '，', '對',... | [['p', 'r', 'e', 

In [9]:
raw_key = ['raw_text', 'cho', 'q']

label_ds = DataSet({'target':[0, 1]})
label_vocab  = Vocabulary(unknown=None, padding=None).from_dataset(label_ds, field_name='target')
char_vocab = Vocabulary()
char_vocab.from_dataset(*ds.values(), field_name=raw_key
    ,no_create_entry_dataset=[ds['dev']]
)
char_vocab.index_dataset(*ds.values(), field_name=raw_key)

label_vocab.from_dataset(label_ds, field_name='target')
label_vocab.index_dataset(label_ds, field_name='target')


Vocabulary([0, 1]...)

In [10]:
char_vocab.to_word(0)

'<pad>'

In [11]:
bundle = DataBundle({ 'target':label_vocab}, ds )

In [12]:
set(role_map.values())

{1, 2, 3, 4, 5}

In [13]:
torch.tensor(np.array(['1']).astype(int))

tensor([1])

In [14]:
from torch import nn
from fastNLP.modules import LSTM
import torch
from fastNLP.models.cnn_text_classification import CNNText


class BiLSTMMaxPoolCls(nn.Module):
    def __init__(self, embed, d_model=300, num_layers=1, dropout=0.3):
        super().__init__()
        self.d_model = d_model
        self.embed = embed
        self.num_class = 2 
        self.d_model = d_model
        self.dropout = .2
        num_head = 4
        roleid_size = len(set(role_map.values())) + 1 # pad

        self.role_emb = nn.Embedding(roleid_size, d_model)
        self.emb_enc = EncoderBlock(conv_num=4, d_model=d_model, num_head=num_head, k=7, dropout=0.1)
        self.c_att = nn.MultiheadAttention(d_model, num_head, dropout=self.dropout)
        self.q_att = nn.MultiheadAttention(d_model, num_head, dropout=self.dropout)

        self.lstm = LSTM(d_model, hidden_size=d_model//2, num_layers=num_layers,
                         batch_first=True, bidirectional=True)
        self.bilstm = LSTM(d_model, hidden_size=d_model//2, num_layers=num_layers,
                         batch_first=True, bidirectional=True)
        self.fc = nn.Linear(d_model, self.num_class)


    def forward(self, raw_text, q, cho, roleid, target_onehot=None):  
        PAD = 0
        bsz = raw_text.size(0)
        d_len, q_len, c_len = raw_text.size(-1), q.size(-1), cho.size(-1)

        d_mask = (torch.ones_like(raw_text)*(raw_text==PAD)).bool().view(bsz, 3, d_len)
        q_mask = (torch.ones_like(q)*(q==PAD)).bool().view(bsz, q_len)
        c_mask = (torch.ones_like(cho)*(cho==PAD)).bool().view(bsz, 3, c_len)

        raw_text = raw_text.view(3*bsz, d_len)
        cho = cho.view(3*bsz, c_len)

        
        d_emb = self.embed(raw_text).view(bsz, 3, d_len, self.d_model)
        q_emb = self.embed(q).view(bsz, q_len, self.d_model)
        c_emb = self.embed(cho).view(bsz, 3, c_len, self.d_model)

        role_emb = self.role_emb(torch.from_numpy(roleid.astype(int)).to(device)).view(bsz, 3, d_len, self.d_model)
        # print(role_emb.shape, role_emb.dtype)
        d_emb = d_emb + role_emb

        c = [ele.squeeze(1).transpose(0, 1) for ele in torch.split(c_emb, 1, dim=1)]
        d = [ele.squeeze(1).transpose(0, 1) for ele in torch.split(d_emb, 1, dim=1)]
        d_mask = [ele.squeeze(1) for ele in torch.split(d_mask, 1, dim=1)]
        c_mask = [ele.squeeze(1) for ele in torch.split(c_mask, 1, dim=1)]

        Edc  = [self.c_att(c[i], d[i], d[i], key_padding_mask=d_mask[i])[0] 
                for i in range(3)]
        Eqdc = [self.q_att(q_emb.transpose(0, 1), Edc[i], Edc[i], key_padding_mask=c_mask[i])[0].transpose(0, 1) 
                for i in range(3)]

        Eqdc = torch.stack(Eqdc, dim=1)
        # print(Eqdc.shape)
        Eqdc = Eqdc.view(bsz*3, q_len, self.d_model)

        outputs, _ = self.lstm(Eqdc)
        outputs = outputs[:, -1, :]
        outputs = outputs.view(bsz, 3, self.d_model)
        
        outputs, _ = self.bilstm(outputs)
        outputs = self.fc(outputs)

        if not target_onehot==None:
            loss_fct = nn.CrossEntropyLoss(
                reduction='sum', 
                weight=torch.tensor([0.66, 1.23]).to(outputs),
            )
            outputs = outputs.view(-1, self.num_class)
            # print(outputs.shape, target_onehot.view(-1).shape)
            # print(outputs.dtype)
            loss = loss_fct(outputs, target_onehot.view(-1).to(torch.long)) / bsz
            pred = torch.max(outputs.view(bsz, 3, self.num_class), dim=1).indices[:, 1]
            return {'pred':pred, 'loss':loss} 
        
        logits = outputs.view(bsz, 3, self.num_class)
        pred = torch.max(logits, dim=1).indices[:, 1]
        return {'pred':pred, 'logits':outputs} 


In [15]:

from fastNLP.embeddings import BertEmbedding
import torch.nn.functional as F

# embed = StackEmbedding([
#     StaticEmbedding(char_vocab, model_dir_or_name='cn-fasttext'),
#     # StaticEmbedding(char_vocab, model_dir_or_name='cn-sgns-literature-word')
# ])
# embed = BertEmbedding(
#     char_vocab, model_dir_or_name='cn-wwm-ext', layers='1')

# print('Embedding shape', embed.embed_size)

In [25]:
vocab = Vocabulary()
vocab.add_word('上海')  
vocab


Vocabulary(['上海']...)

In [28]:
vocab.to_index('上海')

2

In [27]:
embed = StaticEmbedding(vocab, model_dir_or_name='cn-fasttext')


Found 1 out of 3 words in the pre-training embedding.


In [ ]:
embed = StackEmbedding([
    StaticEmbedding(char_vocab, model_dir_or_name='cn-fasttext'),
    # StaticEmbedding(char_vocab, model_dir_or_name='cn-sgns-literature-word'),
    # BertEmbedding(char_vocab, model_dir_or_name='cn-wwm-ext', layers='1'),
])

In [22]:
import fitlog
from fastNLP import Trainer
from fastNLP import CrossEntropyLoss
from torch.optim import Adam, AdamW
from fastNLP import AccuracyMetric
from qanet import *
from fastNLP.core.callback import WarmupCallback,GradientClipCallback,EarlyStopCallback,SaveModelCallback
from fastNLP import FitlogCallback
from fastNLP import LRScheduler
from torch.optim.lr_scheduler import LambdaLR
from fastNLP.core import Callback
from fastNLP.core.callback import WarmupCallback,GradientClipCallback,EarlyStopCallback,SaveModelCallback

fitlog.set_log_dir('./logs')

# fitlog.commit(__file__)             # auto commit your codes


embed = StackEmbedding([
    StaticEmbedding(char_vocab, model_dir_or_name='cn-fasttext'),
    # StaticEmbedding(char_vocab, model_dir_or_name='cn-sgns-literature-word'),
    # BertEmbedding(char_vocab, model_dir_or_name='cn-wwm-ext', layers='1'),
])

# embed = StackEmbedding([StaticEmbedding(char_vocab, model_dir_or_name='cn-fasttext')])
print('Embedding shape', embed.embed_size)

loss = CrossEntropyLoss()
metric = AccuracyMetric()
device = 0 if torch.cuda.is_available() else 'cpu'

for idx in range(1):
  print(f'--------Fold{idx}----------')

  
  model = BiLSTMMaxPoolCls(embed, d_model=embed.embed_size)
#   model = CNNText(embed, 2, dropout=0.2)
  optimizer = AdamW(model.parameters(), lr=3e-4, weight_decay=0.01,)
  # lrschedule_callback = LRScheduler(lr_scheduler=LambdaLR(optimizer, lambda ep: 1 / (1 + 0.05*ep) ))
  clip_callback = GradientClipCallback(clip_type='value', clip_value=2)
 
  trainer = Trainer(
    train_data=bundle.get_dataset(f'train{idx}'), 
    dev_data=bundle.get_dataset(f'val{idx}'),
    model=model, device=device,
    optimizer=optimizer, batch_size=16, n_epochs=10,
    metrics=metric,
    callbacks=[
      # lrschedule_callback,
      clip_callback,
      WarmupCallback(warmup=50,),
      FitlogCallback(),
      # EarlyStopCallback(3),
    ]       
  )
  met = trainer.train()
  print('--------------\n', met, '--------------\n')
fitlog.finish()  


Found 1267 out of 1274 words in the pre-training embedding.
Embedding shape 300
--------Fold0----------
input fields after batch(if batch size is 2):
	raw_text: (1)type:torch.Tensor (2)dtype:torch.int64, (3)shape:torch.Size([2, 3, 245]) 
	cho: (1)type:torch.Tensor (2)dtype:torch.int64, (3)shape:torch.Size([2, 3, 7]) 
	q: (1)type:torch.Tensor (2)dtype:torch.int64, (3)shape:torch.Size([2, 21]) 
	target_onehot: (1)type:torch.Tensor (2)dtype:torch.float32, (3)shape:torch.Size([2, 3]) 
	roleid: (1)type:numpy.ndarray (2)dtype:<U1, (3)shape:(2, 3, 245) 
target fields after batch(if batch size is 2):
	target: (1)type:torch.Tensor (2)dtype:torch.int64, (3)shape:torch.Size([2]) 

training epochs started 2021-06-14-18-18-52-947430


RuntimeError: Cannot set total_steps twice.

In [19]:
from fastNLP.core.predictor import Predictor
pred = Predictor(model).predict(bundle.get_dataset('val0'))['pred']
pred[0:20],pred[20:40],pred[40:60]

([2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2],
 [2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2],
 [2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2])

In [20]:
a = np.array(list(bundle.get_dataset('val0')['target']))
pred = np.array(pred)
np.count_nonzero(a==pred) / a.shape[0]